## Importing Libraries

In [0]:
from pyspark.sql import SparkSession
from pyspark.sql.functions import regexp_replace
from pyspark.sql.functions import col
from pyspark.sql.types import StringType, IntegerType, DoubleType

import pyspark.ml.feature as feats

from pyspark.ml import Pipeline #Build a pipeline
from pyspark.mllib.evaluation import MulticlassMetrics

import pandas as pd


## Creating Spark session

In [0]:
spark = SparkSession.builder.appName('Sentiment140Pretrained').getOrCreate()

## Setting the configuration for Azure Storage Account access

In [0]:
spark.conf.set(
  "fs.azure.account.key.twittergenstorage.blob.core.windows.net",
  "okEjVsoQ+OmK+TNB4/gpnkiDAVNofpG1IxYTOFx+j1JJGQHw9JIk2zakiqyoXm4fmtrAH66vXQB0+AStEZgvtg==")

## Importing the dataset from Azure Storage Account

In [0]:
train = spark.read.format("csv").option("header", "false").load("wasbs://realtimetwitterdata@twittergenstorage.blob.core.windows.net/train-2-3.csv")

In [0]:
display(train)

_c0 _c1 _c2 508566 0 is ready for tomorrow's hangover. how i wonder how it would be?!? rain, rain, rain. I guess i won't be doing laundry after all 1372625 4 Going out! 92958 0 I'm so bored. I wish he was here 1325629 4 @pinktank1 yeah, i was changing it but he seemed excited so i suffered through Barney for him 149409 0 NOOOOO!!!! I'm wearing sandals and just chipped the paint off my big toenail Lookin' silly now. . . 1378228 4 @willie_day26 how was the show? 207120 0 I can't have a sleep over 2nite 105003 0 @quotergal I'm very sad that you and @cabri and @NYPinTA won't be there this year. 479058 0 @aventuredebz not sure what happened there the line just went dead unless you hung up on me 942660 4 @BerlyAnne Again, good daughter, this is true!! 148949 0 Oops, to x "ass" pï¿½ ï¿½n tweet 840452 4 is going to test some pubs before Windays conference 874662 4 eating nachos with my faja, having some daughter/father time 1563939 4 @tartsea hehe, cÃ³ gian dá»i ÄÃ¢u nÃ o, giÃºp báº¡n Ã­ mÃ  1301213 4 Making caleb throw up is great. 1480814 4 I just want to give you guys something nice to look at, & a song to listen to. http://bit.ly/ZWWdv Enjoy. 1363568 4 is going to sleep now... quite early today... 1.03am now... good night... 1132348 4 @tomkelshaw I'm guessing that your mum arrives today? give her a big hug from me 1236389 4 okay, Dear Catastrophe Waitress is so my exam music - I first heard it this time last year 11768 0 @parachutesfail I agree, Saturdays are stupid. I have to work all day as well. 1589849 4 just woke up && ate a bowl of honey cheerios && listening to drive my soul by lights 734253 0 just talked to leonie on the phone. i miiiiiiiss her aha 95523 0 @LaurenOlson and @sgricci thanks for having me over for LOST. We'll have to do it again..... In 2010!!!! 207797 0 ok....the report man took her car... 236623 0 Hang on, NO! They had a close up of the guy STANDING NEXT to me & Hannah, but not us two! 1472256 4 hannah montana was very good. now going to read twilight. 1269314 4 @kristenstewart9 take care of your ankle! btw, congrats on the mtv movie awards 779584 0 wheres the sun at today dammm! im deiyn to mae some music!!!! UC-US Team Movinn Hard!!! 160875 0 @Jordalynn omg you've never seen 'the Ring' its a creppy ass movie 653035 0 @xwheneverx craving for daidomon, crabs, buffets, yum cha. EVERYTHING. 362342 0 my computer is going to crash! 488279 0 still no thunder and lightning 780907 0 laying in bed, nothing to do! cant sleep 1313479 4 Goodnight im working then Chior then movie with taylr and jessica Yay 1328334 4 Newfoundland spring morning, walking around Quidi Vidi Lake I experienced sun, rain, sun and thenâ¦a RAINBOW!..life is good 1561781 4 @ksparkstv heyyyyyy K (yells out government name) hola!!! 646211 0 @Change_for_Iran ultimately he has no choice, not to would be blaming his own President and he wont do that, tough times ahead GOOD LUCK 1199092 4 @ilishe They don't, but they are. 405817 0 didn't catch a single fish. my 2 year old brother caught the biggest of the 3 fish we caught. i'm the only one who didn't catch anything. 1359961 4 @lancearmstrong He's so cute!!! Wishing the proud parents all the best on this little bundle of joy! Congratulations!!! {hugs} 622318 0 It's official! No Atlanta for me this weekend! Instead I'm going to go babysit my "5 little sisters"... 1512815 4 @katelynroseee Happy 17th! I hope that you have an amazing day. Do you feel any different?! 610495 0 I had 525 followers when I started those! LOL... 1326715 4 ugh getting ready for class, exhausted from last night 1177670 4 @risha_ I can't even get into VB Even the server monkeys are mourning 1006859 4 Tired. Had a whole day spent in the school hall. Thank god it's Friday. 111588 0 Hmmm... Tired and sleepy. Yet, nothing much happened. Why??? 1420940 4 @SophieLee_xo i think lee evans is on somewhere too lol next door must think im drunk or something aha xx 144233 0 @cndflybaby at first i thought not the rash lookded different from

## Renaming the columns

In [0]:
train = (train.withColumnRenamed('_c0','row_num')
        .withColumnRenamed('_c1','target')
        .withColumnRenamed('_c2','text')
)

## Replacing the 4 with 1 denoting the Positive Sentiment, 0 denotes the Negative Sentiment

In [0]:
train = train.withColumn('target', regexp_replace('target', '4', '1'))

## Converting target to Integer and creating a final dataframe for training

In [0]:
train = train.withColumn("target", train["target"].cast(IntegerType()))
end_df = train.select(col('text'), col('target'))

end_df.show()

+--------------------+------+
|                text|target|
+--------------------+------+
|is ready for tomo...|     0|
|         Going out! |     1|
|I'm so bored. I w...|     0|
|@pinktank1 yeah, ...|     1|
|NOOOOO!!!! I'm we...|     0|
|@willie_day26 how...|     1|
|I can't have a sl...|     0|
|@quotergal I'm ve...|     0|
|@aventuredebz not...|     0|
|@BerlyAnne Again,...|     1|
|Oops, to x &quot;...|     0|
|is going to test ...|     1|
|eating nachos wit...|     1|
|@tartsea hehe, cÃ...|     1|
|Making caleb thro...|     1|
|I just want to gi...|     1|
|is going to sleep...|     1|
|@tomkelshaw I'm g...|     1|
|okay, Dear Catast...|     1|
|@parachutesfail I...|     0|
+--------------------+------+
only showing top 20 rows



## Installing and importing Spark NLP dependencies

In [0]:
!pip install spark-nlp==4.0.1
import sparknlp
from sparknlp.base import *

     |████████████████████████████████| 531 kB 27.7 MB/s 
You should consider upgrading via the '/local_disk0/.ephemeral_nfs/envs/pythonEnv-f6d04aa2-ec4e-487d-9997-eaefb802f2b3/bin/python -m pip install --upgrade pip' command.


In [0]:
from sparknlp.annotator import *
from sparknlp.pretrained import PretrainedPipeline

In [0]:
# Converting string to Spark NLP document
documentAssembler = DocumentAssembler()\
    .setInputCol("text")\
    .setOutputCol("document")

# Converting Spark NLP document to Spark NLP token in order to perform pre-processing
tokenizer = Tokenizer().setInputCols("document").setOutputCol("token")

# Removing punctuations
normalizer = Normalizer() \
    .setInputCols(["token"]) \
    .setOutputCol("normalized")\
    .setLowercase(True)\
    .setCleanupPatterns(["[^\w\d\s]"]) # remove punctuations (keep alphanumeric chars)
    # if we don't set CleanupPatterns, it will only keep alphabet letters ([^A-Za-z])

# Removing stop words
stopwords_cleaner = StopWordsCleaner()\
      .setInputCols("normalized")\
      .setOutputCol("cleanTokens")\
      .setCaseSensitive(False)\

# Converting back to string
finisher = Finisher().setInputCols("cleanTokens").setOutputCols("output").setOutputAsArray(False).setAnnotationSplitSymbol(' ')

# Converting to document
document_assembler = DocumentAssembler()\
    .setInputCol('output')\
    .setOutputCol('doc')

# Using Sentence Encoder for text vectorization
use = UniversalSentenceEncoder.pretrained(name='tfhub_use', lang='en')\
 .setInputCols(['doc'])\
 .setOutputCol('sentence_embeddings')

# Using SparkNLP pretrained model estimator
sentiment_dl = SentimentDLModel.pretrained(name='sentimentdl_use_twitter', lang='en')\
    .setInputCols(['sentence_embeddings'])\
    .setOutputCol('sentiment')

tfhub_use download started this may take some time.
Approximate size to download 923.7 MB
[OK!]
sentimentdl_use_twitter download started this may take some time.
Approximate size to download 11.4 MB
[OK!]


## Creating the pipeline and fitting the model

In [0]:
pipeline = Pipeline(stages = [documentAssembler,tokenizer,normalizer,stopwords_cleaner,finisher,document_assembler,use,sentiment_dl])

In [0]:
pipelinePreTrain = pipeline.fit(train)

In [0]:
test = spark.read.format("csv").option("header", "false").load("wasbs://realtimetwitterdata@twittergenstorage.blob.core.windows.net/test-2-3.csv")

## Importing the test dataset and performing same pre-processing as the train dataset

In [0]:
test = (test.withColumnRenamed('_c0','row_num')
        .withColumnRenamed('_c1','target')
        .withColumnRenamed('_c2','text')
)

In [0]:
test = test.withColumn('target', regexp_replace('target', '4', '1'))

In [0]:
test = test.withColumn("target", test["target"].cast(IntegerType()))

## Fitting the model pipeline on test dataset and evaluating the results

In [0]:
resultPreTrain = pipelinePreTrain.transform(test)
display(resultPreTrain)

row_num target text output doc sentence_embeddings sentiment 1235522 1 @ColorblindFish Can't wait to see the pics, Thanks colorblindfish cant wait see pics thanks List(List(document, 0, 39, colorblindfish cant wait see pics thanks, Map(sentence -> 0), List())) List(List(sentence_embeddings, 0, 39, colorblindfish cant wait see pics thanks, Map(sentence -> 0, token -> colorblindfish cant wait see pics thanks, pieceId -> -1, isWordStart -> true), List(-0.015589279, -0.08302177, -0.012943912, -0.0043415437, 0.04933013, -0.050999098, 0.0071605328, 0.017707558, 0.036716346, 0.0144419065, 0.003456764, 0.09573679, 0.03956561, -0.009484901, -0.00827883, 0.020734316, -0.02836818, 0.02230314, -0.015361399, 0.06252487, 0.08184971, -0.02920348, -0.034533955, -0.028662303, -0.03802025, -0.09922621, -0.0061737774, -0.029213397, -0.07150137, 0.04158693, -0.06737185, 0.038868897, -0.05630543, 0.04615344, 0.014621475, -0.012141995, -0.08851933, -0.033330195, -0.015459212, -0.068209924, -0.057286248, -0.0153134875, 0.003433841, -0.059675217, -0.017555822, -0.0050070346, -0.033846665, 0.02240671, 0.030342788, -0.009233027, -0.018707713, 0.051701847, -0.02109071, -0.0016756466, 0.06594268, 0.03201248, 0.027238926, -0.0698994, 0.02288257, 0.06916008, 7.0247863E-4, 0.009178041, 0.020019658, -0.0900416, 0.0494402, -0.06387288, 0.05661897, -0.054923568, -0.008712551, -0.010887132, 0.03752841, 0.1014915, -0.02095031, -0.022151645, 0.04401896, -0.02062341, 0.06468485, -0.020410616, 0.009147007, 0.06175821, -0.0063445694, -0.017833509, -0.05198845, 0.04105173, -0.07342199, 7.9603464E-4, 0.03481175, 0.008710402, 0.045426603, -0.029984698, 0.02288133, -0.06859636, -0.0038889218, -0.0244121, 0.02105012, 0.025294216, 0.00977301, -0.06928092, -0.040209204, 0.060817864, 0.031279527, -0.040962305, -0.003250811, 0.032584004, 0.0013871074, -0.013688877, 0.032788724, 0.004877953, -0.012082754, -0.0675661, -0.02609935, -0.00458954, -0.043834858, -0.0065891575, -0.032474298, -0.0021799242, -0.04010175, -0.06298443, 0.043449212, 0.05910532, 0.032723773, 0.022528749, 0.051082477, 0.014778957, 0.033504788, -0.06602424, -0.018617291, -0.0655502, -0.017996391, -0.059435144, -0.08923042, 0.069803424, 0.05681583, 0.061774325, 0.029456705, -0.051781546, -0.04331288, 0.03364724, -0.0067366823, -0.012066911, -0.03275011, -0.060459223, -0.016255556, 0.0084692165, -0.013706349, -0.053644493, 0.07346467, 0.06845349, 0.0037046021, 0.08788184, -0.089565575, -0.07205907, 0.036451124, 0.06693704, 0.008485956, 0.015577237, -0.01691054, -0.045138516, -0.019007035, 0.03031824, -0.03417535, -0.045675628, -0.0036535203, 0.007273435, 0.020225171, -0.02059887, -0.0011234516, 0.030567659, -0.0054899636, -0.06531291, -0.05309563, 0.077644646, 0.013230107, -0.037994623, -0.0120125655, -0.061647844, -0.066644005, -0.023537278, -0.017683288, 0.021958519, -0.08036366, 0.024810774, 0.0610612, 0.05289575, -0.08805721, -0.027623696, 0.06405538, -0.071389794, -0.023821881, -0.040995385, 0.034282953, 0.03643031, 0.015937392, -0.03284471, -0.06349027, -0.0610641, 0.04389488, 0.02080136, 0.055487026, 0.0016885146, 0.04833193, -0.030299496, 0.008885595, 0.0019324853, -0.001723417, -0.009083302, 0.08757961, 0.01442176, 0.020479336, -0.01791506, 0.059996992, -0.021047292, 0.03943092, 0.05833408, -0.019961257, -0.0131790545, 0.057753924, 0.05202982, 0.081078276, 0.068591304, -0.03504864, -0.029818276, -0.013749456, 0.016161948, 0.021462953, -0.0077245217, 0.049432203, 0.020018972, -0.0026732904, -0.04687644, 0.047707655, 0.040997237, -0.007775782, 0.042210504, 0.019115048, -0.038993765, -0.056358833, 0.08157896, -0.019186284, 0.039365895, 0.012794686, 0.0070135337, 0.03648171, -0.09193366, 0.03313261, 0.030851016, 0.058306433, 0.02137795, -0.023047013, 0.076659456, -0.075912826, -0.07476062, 0.055734985, -0.013298387, -0.06697384, 0.04114369, 0.0016706503, 0.036322117, 0.06342017, -0.065266326, 0.033848114, 0.014856255, -0.066856, -0.034854535, -0.017290033, 0.05703432, -0.05447207, 0.08839441, 0.046000652

In [0]:
import pyspark.sql.functions as f

In [0]:
resultPreTrain = resultPreTrain.na.drop()
resultPreTrain = resultPreTrain.filter("output != ''")
display(resultPreTrain)

row_num target text output doc sentence_embeddings sentiment 1235522 1 @ColorblindFish Can't wait to see the pics, Thanks colorblindfish cant wait see pics thanks List(List(document, 0, 39, colorblindfish cant wait see pics thanks, Map(sentence -> 0), List())) List(List(sentence_embeddings, 0, 39, colorblindfish cant wait see pics thanks, Map(sentence -> 0, token -> colorblindfish cant wait see pics thanks, pieceId -> -1, isWordStart -> true), List(-0.015589279, -0.08302177, -0.012943912, -0.0043415437, 0.04933013, -0.050999098, 0.0071605328, 0.017707558, 0.036716346, 0.0144419065, 0.003456764, 0.09573679, 0.03956561, -0.009484901, -0.00827883, 0.020734316, -0.02836818, 0.02230314, -0.015361399, 0.06252487, 0.08184971, -0.02920348, -0.034533955, -0.028662303, -0.03802025, -0.09922621, -0.0061737774, -0.029213397, -0.07150137, 0.04158693, -0.06737185, 0.038868897, -0.05630543, 0.04615344, 0.014621475, -0.012141995, -0.08851933, -0.033330195, -0.015459212, -0.068209924, -0.057286248, -0.0153134875, 0.003433841, -0.059675217, -0.017555822, -0.0050070346, -0.033846665, 0.02240671, 0.030342788, -0.009233027, -0.018707713, 0.051701847, -0.02109071, -0.0016756466, 0.06594268, 0.03201248, 0.027238926, -0.0698994, 0.02288257, 0.06916008, 7.0247863E-4, 0.009178041, 0.020019658, -0.0900416, 0.0494402, -0.06387288, 0.05661897, -0.054923568, -0.008712551, -0.010887132, 0.03752841, 0.1014915, -0.02095031, -0.022151645, 0.04401896, -0.02062341, 0.06468485, -0.020410616, 0.009147007, 0.06175821, -0.0063445694, -0.017833509, -0.05198845, 0.04105173, -0.07342199, 7.9603464E-4, 0.03481175, 0.008710402, 0.045426603, -0.029984698, 0.02288133, -0.06859636, -0.0038889218, -0.0244121, 0.02105012, 0.025294216, 0.00977301, -0.06928092, -0.040209204, 0.060817864, 0.031279527, -0.040962305, -0.003250811, 0.032584004, 0.0013871074, -0.013688877, 0.032788724, 0.004877953, -0.012082754, -0.0675661, -0.02609935, -0.00458954, -0.043834858, -0.0065891575, -0.032474298, -0.0021799242, -0.04010175, -0.06298443, 0.043449212, 0.05910532, 0.032723773, 0.022528749, 0.051082477, 0.014778957, 0.033504788, -0.06602424, -0.018617291, -0.0655502, -0.017996391, -0.059435144, -0.08923042, 0.069803424, 0.05681583, 0.061774325, 0.029456705, -0.051781546, -0.04331288, 0.03364724, -0.0067366823, -0.012066911, -0.03275011, -0.060459223, -0.016255556, 0.0084692165, -0.013706349, -0.053644493, 0.07346467, 0.06845349, 0.0037046021, 0.08788184, -0.089565575, -0.07205907, 0.036451124, 0.06693704, 0.008485956, 0.015577237, -0.01691054, -0.045138516, -0.019007035, 0.03031824, -0.03417535, -0.045675628, -0.0036535203, 0.007273435, 0.020225171, -0.02059887, -0.0011234516, 0.030567659, -0.0054899636, -0.06531291, -0.05309563, 0.077644646, 0.013230107, -0.037994623, -0.0120125655, -0.061647844, -0.066644005, -0.023537278, -0.017683288, 0.021958519, -0.08036366, 0.024810774, 0.0610612, 0.05289575, -0.08805721, -0.027623696, 0.06405538, -0.071389794, -0.023821881, -0.040995385, 0.034282953, 0.03643031, 0.015937392, -0.03284471, -0.06349027, -0.0610641, 0.04389488, 0.02080136, 0.055487026, 0.0016885146, 0.04833193, -0.030299496, 0.008885595, 0.0019324853, -0.001723417, -0.009083302, 0.08757961, 0.01442176, 0.020479336, -0.01791506, 0.059996992, -0.021047292, 0.03943092, 0.05833408, -0.019961257, -0.0131790545, 0.057753924, 0.05202982, 0.081078276, 0.068591304, -0.03504864, -0.029818276, -0.013749456, 0.016161948, 0.021462953, -0.0077245217, 0.049432203, 0.020018972, -0.0026732904, -0.04687644, 0.047707655, 0.040997237, -0.007775782, 0.042210504, 0.019115048, -0.038993765, -0.056358833, 0.08157896, -0.019186284, 0.039365895, 0.012794686, 0.0070135337, 0.03648171, -0.09193366, 0.03313261, 0.030851016, 0.058306433, 0.02137795, -0.023047013, 0.076659456, -0.075912826, -0.07476062, 0.055734985, -0.013298387, -0.06697384, 0.04114369, 0.0016706503, 0.036322117, 0.06342017, -0.065266326, 0.033848114, 0.014856255, -0.066856, -0.034854535, -0.017290033, 0.05703432, -0.05447207, 0.08839441, 0.046000652

In [0]:
sentiment_result = resultPreTrain.withColumn('doc', f.explode('doc')).withColumn('sentiment', f.explode('sentiment')).select(col('doc.result').alias('doc'), col('sentiment.result').alias('sentiment'), 'target')

sentiment_result.show(truncate=False)

+---------------------------------------------------------------------------------------------+---------+------+
|doc                                                                                          |sentiment|target|
+---------------------------------------------------------------------------------------------+---------+------+
|colorblindfish cant wait see pics thanks                                                     |positive |1     |
|fests                                                                                        |positive |1     |
|missed live chat selena gomez                                                                |positive |0     |
|goodnight thanks robbie help today amazing                                                   |positive |1     |
|hot day im crowded busthis isnt pleasant                                                     |negative |0     |
|wolfchild59 heh send dem get dem jen shocked found many last days earlier week nothing       |n

In [0]:
RESULT_MAP = { 'positive': 1, 'negative':0, 'neutral':2 }

@udf(returnType=IntegerType())
def map_results(text):
    return RESULT_MAP[text]

In [0]:
sentiment_result = sentiment_result.na.drop()

final_result = sentiment_result.withColumn('result', map_results(col('sentiment')))

final_result.show()

+--------------------+---------+------+------+
|                 doc|sentiment|target|result|
+--------------------+---------+------+------+
|colorblindfish ca...| positive|     1|     1|
|               fests| positive|     1|     1|
|missed live chat ...| positive|     0|     1|
|goodnight thanks ...| positive|     1|     1|
|hot day im crowde...| negative|     0|     0|
|wolfchild59 heh s...| negative|     1|     0|
|lakers baby sad c...| negative|     0|     0|
|theundomestic thi...| positive|     1|     1|
|anybody know some...| negative|     0|     0|
|              bombed| negative|     0|     0|
|gonna get try cat...| negative|     0|     0|
|witchwithkids got...| negative|     0|     0|
|deneki im sure so...| negative|     1|     0|
|jub0o hey u big p...| positive|     1|     1|
|nathanmillson gra...| positive|     1|     1|
|skrishna figured ...| negative|     1|     0|
|good daynow sleep...| positive|     1|     1|
|feelin sick today...| negative|     0|     0|
|eurghh super

In [0]:
predictionAndLabels = final_result.select('target', 'result')

metrics = MulticlassMetrics(predictionAndLabels.rdd.map(lambda x: tuple(map(float, x))))

/databricks/spark/python/pyspark/sql/context.py:165: FutureWarning: Deprecated in 3.0.0. Use SparkSession.builder.getOrCreate() instead.
  warnings.warn(


In [0]:
confusion_matrix = metrics.confusionMatrix().toArray()
labels = [int(label) for label in metrics.call('labels')]
pd.DataFrame(confusion_matrix , index=labels, columns=labels)

0 
 1 
 2 
 
 
 
 
 0 
 11472.0 
 2727.0 
 0.0 
 
 
 1 
 4190.0 
 12884.0 
 0.0 
 
 
 2 
 889.0 
 822.0 
 0.0

In [0]:
print('Summary Stats')
print(f'Accuracy: {metrics.accuracy:.4f}')
print(f'False positive rate: {metrics.weightedFalsePositiveRate:.4f}')
print(f'False positive rate: {metrics.weightedFMeasure():.4f}')

Summary Stats
Accuracy: 0.7384
False positive rate: 0.2319
False positive rate: 0.7193
